# Prepare Leaf type data from TRY for use

The leaf type data from TRY informs on the basic leaf morphology (note that there is also
leaf shape). Leaf type rather refers to the overall appearance of a plant than to the detailed
description of its leaves.

*If you intend to clean more than one or two traits, we recommend the use
of the batch pre-processing script. Refer to the [TRY main page](try-label) for details.*

If you have questions, suggestions, spot errors, or want to contribute, get in touch with us through planthub@idiv.de.

Author: David Schellenberger Costa

## Requirements

To run the script, the following is needed:
- TRY data, available <a href="https://planthub.idiv.de/downloads/" target="_parent">here</a>
- the data.table library may need to be installed

## Code

In [ ]:
# load in libraries
library(data.table) # handle large datasets

# clear workspace
rm(list = ls())


Let's get the TRY data

In [ ]:
# set working directory (adapt this!)
setwd(paste0(.brd, "PlantHub"))

# read in data (adapt this!)
TRY <- fread("TRY_PlantHub.gz")

# select data of interest#select data of interest
TRYSubset <- TRY[TraitName == "Leaf type"]


To get an overview of the data, we convert values to lowercase, sort them, and show them as
a table.

In [ ]:
# extract original data strings
oriVals <- TRYSubset$OrigValueStr # oriVals == original values

# change all to lowercase to ease later classification
oriVals <- tolower(oriVals)

# get an overview over the data by summarizing values and showing them in alphabetical order
valueOverview <- table(oriVals)
valueOverview[order(valueOverview)]


Apparently, there are some trait categories mixed here. We will prepare a matrix with two columns
to separately save entries describing leaf shape and stem photosynthesis.

In [ ]:
newVals <- matrix(NA, length(oriVals), 2)


The most important part of the cleaning process is the definition of the search strings to look for.
We use regular expressions in some cases to be more inclusive (or exclusive).

In [ ]:
searchNames <- c(
	"aphyll|leafless|without leaves",
	"broad\\-?lea(f|v)|^B$|^broad( ?leaved)?$",
	"fine|lanceolate|linear|narrow\\-?lea(f|v)|^N$",
	"needle",
	"scale|micro",
	"conifer|^C$",
	"cylindric",
	"emersed|floating|submersed",
	"photosynthetic stem"
)


We can now search for the strings defined before and give names to the new categories.

In [ ]:
# search for the strings defined before
searchResults <- sapply(searchNames, grepl, oriVals)

# name columns of searchResults matrix like corrected searchNames
colnames(searchResults) <- c(
	"aphyllous", "elliptic", "oblong", "needle", "scale",
	"coniferous", "cylindric", "aquatic", "photosynthetic stem"
)


Let's have a look at the results.

In [ ]:
# show the number of matches to each category
colSums(searchResults)

# show the original entries for which no match was retrieved
oriVals[rowSums(searchResults) < 1]

# show the number of entries that weren't matched to any category
sum(rowSums(searchResults) < 1)

# show the number of entries that were matched to more that one category
sum(rowSums(searchResults) > 1)


As some categories should be exclusive, we exclude all ambiguous data
by setting our search results to FALSE whenever we found more than
one match in our search.

In [ ]:
searchResults[searchResults[, 1] == TRUE & rowSums(searchResults[, 1:8]) > 1, 1:8] <- FALSE # aphyllous
searchResults[searchResults[, 7] == TRUE & rowSums(searchResults[, 1:7]) > 1, 1:7] <- FALSE # cylindric
searchResults[searchResults[, 2] == TRUE & rowSums(searchResults[, 2:5]) > 1, 2:5] <- FALSE # broad-leaved
searchResults[searchResults[, 3] == TRUE & rowSums(searchResults[, 2:5]) > 1, 2:5] <- FALSE # narrow-leaved


Now, we can create new strings with the cleaned values and add them to the observations. To
not remove the original entries, we will create a new column called "CleanedValueStr". We separate
entries relating to leaf shape and stem photosynthesis and change the trait names accordingly.

In [ ]:
newVals[, 1] <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[c(1:8)][searchResults[x, c(1:8)]], collapse = ",")
})
newVals[, 2] <- sapply(seq_len(nrow(searchResults)), function(x) {
	paste(colnames(searchResults)[9][searchResults[x, 9]], collapse = ",")
})
newVals[newVals == ""] <- NA

# move values to other traits
TRY[TraitName == "Leaf type", CleanedValueStr := newVals[, 2]]
TRY[TraitName == "Leaf type", TraitName := "gotoStem photosynthesis"]
TRY[TraitName == "gotoStem photosynthesis" & CleanedValueStr == "photosynthetic stem", CleanedValueStr := TRUE]
TRY <- rbind(TRY, TRYSubset, fill = TRUE)

# integrate into TRY
TRY[TraitName == "Leaf type", CleanedValueStr := newVals[, 1]]
# 'Leaf phenology type', 'Leaf shape', and 'Leaf type' have overlapping categories, move all to 'Leaf shape'
TRY[TraitName == "Leaf type", TraitName := "gotoLeaf shape"]


As we duplicated the data to accommodate the data belonging to other traits, to avoid an unnecessary increase
in file size, we remove the rows of the duplicated data without values in the "CleanedValueStr" column.

In [ ]:
TRY <- TRY[!grepl("^goto", TraitName) | !is.na(CleanedValueStr)]


We have used an existing trait name with the prefix "goto" to classify some data. This was done
to eventually move the data to the respective trait, but avoid another round of pre-processing.
So only run the following line if this is the last of various pre-processing scripts you want to use.

In [ ]:
TRY[, TraitName := sub("^goto", "", TraitName)]


Let's write the data to a file.

In [ ]:
fwrite(TRY, file = paste0("TRY_processed_", Sys.Date(), ".gz"))
